In [1]:
!pip install pandas ydata-profiling scikit-learn

In [2]:
import pandas as pd
from ydata_profiling import ProfileReport
from sklearn.model_selection import train_test_split
from imblearn.under_sampling import RandomUnderSampler
import matplotlib.pyplot as plt

In [3]:
CSV_FILE_NAME = 'Datos_Examen 11.csv'  # Extracted Constant
exam_data = pd.read_csv(CSV_FILE_NAME, sep=';')  # Renaming, Change Function Signature

In [4]:
len(exam_data)

3276

In [5]:
train, test = train_test_split(exam_data, test_size=0.2, random_state=77)

## Exploración de los datos

In [6]:
ProfileReport(train)

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

## Hallazgos

Se encontraron los siguientes problemas a tener en cuenta con los datos:
- Las variables: pH, Sulfatos, Trihalometanos tienen valores faltantes
- La variable-objetivo no está balanceada
- Todas las variables se distribuyen de forma normal


## Limpieza

- Para el primer problema se optó por remover los datos con valores faltantes, esto debido a que estos no son demasiados.
- En cuanto al balanceo de los datos se utilizó under sampling, ya que sé cuanta con suficientes observaciones
- Ya que las variables se distribuyen de forma normal de ser necesario hacer un cambio de escala se usara un standard-scaler


In [8]:
train.dropna(inplace=True)
X_train = train.drop(columns = ['Potabilidad'])
y_train = train['Potabilidad'].map(lambda x: int(x=='SI'))

rus = RandomUnderSampler(random_state=77)
X_train_res, y_train_res = rus.fit_resample(X_train, y_train)

In [9]:
y_train_res.value_counts()

Potabilidad
0    653
1    653
Name: count, dtype: int64

In [10]:
test.dropna(inplace=True)
X_test = test.drop(columns = ['Potabilidad'])
y_test = test['Potabilidad'].map(lambda x: int(x=='SI'))

## Modelo re regression logística

En este caso se hizo un cambio de escala para acelerar la convergencia del modelo


In [11]:
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import GridSearchCV
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import classification_report

std_scaler = StandardScaler()
X_train_scaled = std_scaler.fit_transform(X_train_res)

params = {'C': [0.1, 0.5, 1]}

logistic = LogisticRegression()

grid_search = GridSearchCV(logistic, param_grid=params, cv=5)
grid_search.fit(X_train_scaled, y_train_res)

print(f'Best parameters: {grid_search.best_params_}')
print(f'Best score: {grid_search.best_score_}')

logistic_best = LogisticRegression(C=grid_search.best_params_["C"])
logistic_best.fit(X_train_scaled, y_train_res)

y_pred_test = logistic_best.predict(std_scaler.transform(X_test))
print(classification_report(y_test, y_pred_test))

Best parameters: {'C': 0.5}
Best score: 0.5176157468339622
              precision    recall  f1-score   support

           0       0.59      0.51      0.55       232
           1       0.40      0.47      0.43       158

    accuracy                           0.50       390
   macro avg       0.49      0.49      0.49       390
weighted avg       0.51      0.50      0.50       390


## Modelo Random Forest

Este modelo no es sensible a las escalas y, por lo tanto, no se hizo un cambio de escala

In [13]:
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import GridSearchCV

param_grid = {
    'criterion': ['gini', 'entropy'],
    'max_depth': [4, 6, 8, 10],
    'min_samples_split': [3, 4, 5]
}

rf = RandomForestClassifier(class_weight='balanced')

grid_search_rf = GridSearchCV(estimator=rf, param_grid=param_grid, cv=5)

grid_search_rf.fit(X_train_res, y_train_res)

print(f"Best parameters: {grid_search_rf.best_params_}")
print(f"Best score: {grid_search_rf.best_score_}")

rf_best = RandomForestClassifier(**grid_search_rf.best_params_)
rf_best.fit(X_train_res, y_train_res)

y_pred_test_rf = rf_best.predict(X_test)
print(classification_report(y_test, y_pred_test_rf))

Best parameters: {'criterion': 'gini', 'max_depth': 10, 'min_samples_split': 3}
Best score: 0.643956011815975
              precision    recall  f1-score   support

           0       0.72      0.73      0.73       232
           1       0.60      0.59      0.59       158

    accuracy                           0.67       390
   macro avg       0.66      0.66      0.66       390
weighted avg       0.67      0.67      0.67       390


## KNN

En este caso se usó el standard-scaler, ya que el modelo es sensible a la escala. Esto es debido a que usa métrica de distancia para conseguir sus resultados.

In [14]:
from sklearn.model_selection import GridSearchCV
from sklearn.neighbors import KNeighborsClassifier

std_scaler = StandardScaler()
X_train_scaled = std_scaler.fit_transform(X_train_res)

param_grid = {'n_neighbors': [1, 2, 3, 4, 5]}

knn = KNeighborsClassifier()

grid_search_knn = GridSearchCV(knn, param_grid, cv=5)

grid_search_knn.fit(X_train_scaled, y_train_res)

print("Best K:", grid_search_knn.best_params_)
print("Best score:", grid_search_knn.best_score_)

knn = KNeighborsClassifier(n_neighbors=grid_search_knn.best_params_['n_neighbors'])
knn.fit(X_train_scaled, y_train_res)

X_test_scaled = std_scaler.transform(X_test)
y_pred_test_knn = knn.predict(X_test_scaled)
print(classification_report(y_test, y_pred_test_knn))


Best K: {'n_neighbors': 5}
Best score: 0.6041589892076862
              precision    recall  f1-score   support

           0       0.67      0.65      0.66       232
           1       0.50      0.53      0.51       158

    accuracy                           0.60       390
   macro avg       0.58      0.59      0.59       390
weighted avg       0.60      0.60      0.60       390


## Naive Bayes

En este caso Bayes es independiente de la escala

In [15]:
from sklearn.naive_bayes import GaussianNB
from sklearn.metrics import classification_report

gnb = GaussianNB()

gnb.fit(X_train_res, y_train_res)

y_pred = gnb.predict(X_test)

report = classification_report(y_test, y_pred)

print(report)

              precision    recall  f1-score   support

           0       0.65      0.70      0.68       232
           1       0.51      0.46      0.48       158

    accuracy                           0.60       390
   macro avg       0.58      0.58      0.58       390
weighted avg       0.59      0.60      0.60       390


In [16]:
from sklearn.metrics import precision_score, recall_score, accuracy_score, f1_score

models = [logistic_best, rf_best, knn, gnb]
models_X_test = [X_test_scaled, X_test, X_test_scaled, X_test]

results_comparison = pd.DataFrame({
    'model':[type(model).__name__ for model in models],
    'precision': [precision_score(y_test, model.predict(X), average='binary') for model, X in zip(models, models_X_test)],
    'recall': [recall_score(y_test, model.predict(X), average='binary') for model, X in zip(models, models_X_test)],
    'accuracy': [accuracy_score(y_test, model.predict(X)) for model, X in zip(models, models_X_test)],
    'f1': [f1_score(y_test, model.predict(X), average='binary') for model, X in zip(models, models_X_test)]
})

results_comparison

model  precision    recall  accuracy        f1
0      LogisticRegression   0.398936  0.474684  0.497436  0.433526
1  RandomForestClassifier   0.600000  0.588608  0.674359  0.594249
2    KNeighborsClassifier   0.503030  0.525316  0.597436  0.513932
3              GaussianNB   0.507042  0.455696  0.600000  0.480000

In [17]:
from sklearn.tree import DecisionTreeClassifier
from sklearn.metrics import classification_report

dtc = DecisionTreeClassifier(max_depth=3)

dtc.fit(X_train_res, y_train_res)

y_pred = dtc.predict(X_test)

report = classification_report(y_test, y_pred)

print(report)

              precision    recall  f1-score   support

           0       0.63      0.82      0.71       232
           1       0.52      0.29      0.37       158

    accuracy                           0.61       390
   macro avg       0.58      0.56      0.54       390
weighted avg       0.59      0.61      0.57       390


In [18]:
from sklearn import tree

print(tree.export_text(dtc))

|--- feature_4 <= 260.75
|   |--- feature_0 <= 6.10
|   |   |--- feature_2 <= 27954.17
|   |   |   |--- class: 0
|   |   |--- feature_2 >  27954.17
|   |   |   |--- class: 1
|   |--- feature_0 >  6.10
|   |   |--- feature_2 <= 8689.68
|   |   |   |--- class: 0
|   |   |--- feature_2 >  8689.68
|   |   |   |--- class: 1
|--- feature_4 >  260.75
|   |--- feature_4 <= 387.33
|   |   |--- feature_1 <= 165.31
|   |   |   |--- class: 1
|   |   |--- feature_1 >  165.31
|   |   |   |--- class: 0
|   |--- feature_4 >  387.33
|   |   |--- feature_0 <= 7.91
|   |   |   |--- class: 1
|   |   |--- feature_0 >  7.91
|   |   |   |--- class: 0


## Análisis de resultados

Una vez construido los modelos, debería estar en capacidad de responder estas preguntas:

- ¿Qué puedes decir de los valores de las métricas recall y precisión para cada una de las clases en cada
modelo?
    - Ambos son bajos 
- ¿Cuál de estás métricas considera que es más importante con base en la descripción del problema?
    - En este caso la precision debería tomar más importancia, ya que el costo de afirmar que una fuente de agua es potable cuando no lo es, es mayor. Hacer esto podría significar herir la salud de los usuarios del modelo 
- ¿Considera que el rendimiento de los modelos es adecuado? Si no es así, ¿cómo podrían mejorarse los
resultados?
    - No, ya que incluso para el mejor modelo, cuando este detecta el agua como potable hay una probabilidad de ~42% de que no lo sea. Incluso como una herramienta exploratoria no se puede esperar mucho, porque solo es 8 puntos porcentuales mejor que el azar.
- ¿Cuáles son las variables más significativas según el mejor modelo basado en árboles de decisión? Reflexione
sobre cómo este nuevo conocimiento podría ayudar a tomar decisiones en el contexto del problema.
    - El nivel de sulfatos y carbono orgánico parecen ser las variables más relevantes. Esto nos puede ayudar a saber cuáles son las fuentes de contaminación más importantes. Por ejemplo, un alto nivel de sulfatos podría indicar contaminación debido a fertilizantes.
- Si los cuatro modelos proporcionan resultados similares en cuanto a las métricas de rendimiento ¿Cuál
seleccionaría tomando en cuenta el contexto del problema?
    - El modelo de árboles de decision, no únicamente porque fue él consiguió los mejores resultados, sino porque este también puede ser entendido fácilmente.